Note: this won't work on your system unless you download the datasets and order them in the same way I have

In [2]:
import pandas as pd
import numpy as np
import io
import os
import altair as alt

In [3]:
# Import datetime so we can treat date columns as such and perform operations
from datetime import datetime as dt

Imports of packages

In [4]:
#os.chdir("C:\\Users\\Alexa\\OneDrive\\Ottawa U\\Year 4\\Fall\\MAT4376 - Data Analysis\\Project 1")
# set this to wherever the provided dataset is located

In [5]:
os.getcwd()

'C:\\Users\\awyat049\\OneDrive\\Ottawa U\\Year 4\\Fall\\MAT4376 - Data Analysis\\Project 1\\MAT4376-P1'

In [6]:
as_data = pd.read_csv('polls_us_election_2016.csv')

In [7]:
whole_data = pd.read_csv('Dataset_assigned_data_taken_from/president_general_polls_2016.csv')

In [56]:
poll_raw_years = pd.read_csv('2016_Pollster_Ratings/raw-polls.csv')

In [9]:
poll_ratings_bias = pd.read_csv('2016_Pollster_Ratings/pollster-stats-full.csv')

In [10]:
poll_raw_years.columns

Index(['poll_id', 'question_id', 'race_id', 'year', 'race', 'location',
       'type_simple', 'type_detail', 'pollster', 'pollster_rating_id',
       'methodology', 'partisan', 'polldate', 'samplesize', 'cand1_name',
       'cand1_id', 'cand1_party', 'cand1_pct', 'cand2_name', 'cand2_id',
       'cand2_party', 'cand2_pct', 'cand3_pct', 'margin_poll', 'electiondate',
       'cand1_actual', 'cand2_actual', 'margin_actual', 'error', 'bias',
       'rightcall', 'advancedplusminus', 'comment'],
      dtype='object')

In [57]:
# convert all dates into datetime format
as_data['startdate'] = as_data['startdate'].astype('datetime64')
as_data['enddate'] = as_data['enddate'].astype('datetime64')
whole_data['startdate'] = whole_data['startdate'].astype('datetime64')
whole_data['enddate'] = whole_data['enddate'].astype('datetime64')
# Note: forecast date in whole_data is WRONG - interpreted month as year
poll_raw_years['polldate'] = poll_raw_years['polldate'].astype('datetime64')
poll_raw_years['electiondate'] = poll_raw_years['electiondate'].astype('datetime64')

In [58]:
#only 2016 polls

poll_raw_years = poll_raw_years[poll_raw_years['year'] == 2016]
poll_raw_years['electiondate'].unique

<bound method Series.unique of 7634   2016-02-01
7635   2016-02-01
7636   2016-02-01
7637   2016-02-01
7638   2016-02-01
          ...    
9003   2016-11-08
9004   2016-12-10
9005   2016-12-10
9006   2016-12-10
9007   2016-12-10
Name: electiondate, Length: 1374, dtype: datetime64[ns]>

In [65]:
# match pols from 'whole_data' and 'poll_raw_years'
# first cut down 'poll_raw_years' to just 2016 and just November Elections


poll_raw_years = poll_raw_years[poll_raw_years['electiondate'] == np.datetime64('2016-11-08')]

#contributor_polls = poll_raw_years[poll_raw_years['pollster']=='Gravis Marketing/Kaplan Strategies']
#contributor_polls
poll_raw_years = poll_raw_years[poll_raw_years['type_simple'] == 'Pres-G']
poll_raw_years.columns

Index(['poll_id', 'question_id', 'race_id', 'year', 'race', 'location',
       'type_simple', 'type_detail', 'pollster', 'pollster_rating_id',
       'methodology', 'partisan', 'polldate', 'samplesize', 'cand1_name',
       'cand1_id', 'cand1_party', 'cand1_pct', 'cand2_name', 'cand2_id',
       'cand2_party', 'cand2_pct', 'cand3_pct', 'margin_poll', 'electiondate',
       'cand1_actual', 'cand2_actual', 'margin_actual', 'error', 'bias',
       'rightcall', 'advancedplusminus', 'comment'],
      dtype='object')

In [72]:
as_data.columns

Index(['state', 'startdate', 'enddate', 'pollster', 'grade', 'samplesize',
       'population', 'rawpoll_clinton', 'rawpoll_trump', 'rawpoll_johnson',
       'rawpoll_mcmullin', 'adjpoll_clinton', 'adjpoll_trump',
       'adjpoll_johnson', 'adjpoll_mcmullin', 'lengthofsurveydaysint'],
      dtype='object')

In [67]:
# select all cells from original set that have a 'poll_id', 'question_id', 'samplesize'

final_matched_set = whole_data[whole_data['poll_id'].isin(poll_raw_years['poll_id'].unique())]
final_matched_set

cycle     branch        type                        matchup  \
0       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
1       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
2       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
3       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
4       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
...      ...        ...         ...                            ...   
10711   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
10726   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
10729   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
10800   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
11071   2016  President  polls-only  Clinton vs. Trump vs. Johnson   

      forecastdate           state  startdate    enddate  \
0          11/8/16            U.S. 2016-11-03 2016-11-06   
1          11/8/16            U.S. 2016-11-01 2016-11-07   
2          11/8/16            U.S. 2016-11-02 2016-11-06   
3          11/8/16            U.S. 2016-11-04 2016-11-07   
4          11/8/16            U.S. 2016-11-03 2016-11-06   
...            ...             ...        ...        ...   
10711      11/8/16         Florida 2016-10-25 2016-10-31   
10726      11/8/16        Michigan 2016-10-25 2016-10-31   
10729      11/8/16  North Carolina 2016-10-25 2016-10-31   
10800      11/8/16            U.S. 2016-10-18 2016-10-20   
11071      11/8/16            U.S. 2016-10-17 2016-10-23   

                       pollster grade  ...  adjpoll_clinton adjpoll_trump  \
0      ABC News/Washington Post    A+  ...         45.20163      41.72430   
1       Google Consumer Surveys     B  ...         43.34557      41.21439   
2                         Ipsos    A-  ...         42.02638      38.81620   
3                        YouGov     B  ...         45.65676      40.92004   
4              Gravis Marketing    B-  ...         46.84089      42.33184   
...                         ...   ...  ...              ...           ...   
10711              SurveyMonkey    C-  ...         44.64055      45.48589   
10726              SurveyMonkey    C-  ...         41.64558      42.50747   
10729              SurveyMonkey    C-  ...         45.62324      44.41153   
10800  The Times-Picayune/Lucid   NaN  ...         45.34765      41.99739   
11071              SurveyMonkey    C-  ...         44.56214      42.97135   

       adjpoll_johnson  adjpoll_mcmullin  multiversions  \
0             4.626221               NaN            NaN   
1             5.175792               NaN            NaN   
2             6.844734               NaN            NaN   
3             6.069454               NaN            NaN   
4             3.726098               NaN            NaN   
...                ...               ...            ...   
10711         2.020044               NaN            NaN   
10726         5.020043               NaN            NaN   
10729         4.020043               NaN            NaN   
10800         3.061498               NaN            NaN   
11071         3.088467               NaN            NaN   

                                                     url  poll_id  \
0      https://www.washingtonpost.com/news/the-fix/wp...    48630   
1      https://datastudio.google.com/u/0/#/org//repor...    48847   
2      http://projects.fivethirtyeight.com/polls/2016...    48922   
3      https://d25d2506sfb94s.cloudfront.net/cumulus_...    48687   
4      http://www.gravispolls.com/2016/11/final-natio...    48848   
...                                                  ...      ...   
10711  https://www.surveymonkey.com/elections/map?pol...    47892   
10726  https://www.surveymonkey.com/elections/map?pol...    47905   
10729  https://www.surveymonkey.com/elections/map?pol...    47916   
10800          https://luc.id/2016-presidential-tracker/    47163   
11071  https://www.scribd.com/document/328753246/NBC

In [70]:
final_matched_set = final_matched_set[final_matched_set['question_id'].isin(poll_raw_years['question_id'].unique())]
final_matched_set

cycle     branch        type                        matchup  \
1       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
2       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
3       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
4       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
8       2016  President  polls-plus  Clinton vs. Trump vs. Johnson   
...      ...        ...         ...                            ...   
10711   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
10726   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
10729   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
10800   2016  President  polls-only  Clinton vs. Trump vs. Johnson   
11071   2016  President  polls-only  Clinton vs. Trump vs. Johnson   

      forecastdate           state  startdate    enddate  \
1          11/8/16            U.S. 2016-11-01 2016-11-07   
2          11/8/16            U.S. 2016-11-02 2016-11-06   
3          11/8/16            U.S. 2016-11-04 2016-11-07   
4          11/8/16            U.S. 2016-11-03 2016-11-06   
8          11/8/16      New Mexico 2016-11-06 2016-11-06   
...            ...             ...        ...        ...   
10711      11/8/16         Florida 2016-10-25 2016-10-31   
10726      11/8/16        Michigan 2016-10-25 2016-10-31   
10729      11/8/16  North Carolina 2016-10-25 2016-10-31   
10800      11/8/16            U.S. 2016-10-18 2016-10-20   
11071      11/8/16            U.S. 2016-10-17 2016-10-23   

                       pollster grade  ...  adjpoll_clinton adjpoll_trump  \
1       Google Consumer Surveys     B  ...         43.34557      41.21439   
2                         Ipsos    A-  ...         42.02638      38.81620   
3                        YouGov     B  ...         45.65676      40.92004   
4              Gravis Marketing    B-  ...         46.84089      42.33184   
8                      Zia Poll   NaN  ...         44.82594      41.59978   
...                         ...   ...  ...              ...           ...   
10711              SurveyMonkey    C-  ...         44.64055      45.48589   
10726              SurveyMonkey    C-  ...         41.64558      42.50747   
10729              SurveyMonkey    C-  ...         45.62324      44.41153   
10800  The Times-Picayune/Lucid   NaN  ...         45.34765      41.99739   
11071              SurveyMonkey    C-  ...         44.56214      42.97135   

       adjpoll_johnson  adjpoll_mcmullin  multiversions  \
1             5.175792               NaN            NaN   
2             6.844734               NaN            NaN   
3             6.069454               NaN            NaN   
4             3.726098               NaN            NaN   
8             7.870127               NaN            NaN   
...                ...               ...            ...   
10711         2.020044               NaN            NaN   
10726         5.020043               NaN            NaN   
10729         4.020043               NaN            NaN   
10800         3.061498               NaN            NaN   
11071         3.088467               NaN            NaN   

                                                     url  poll_id  \
1      https://datastudio.google.com/u/0/#/org//repor...    48847   
2      http://projects.fivethirtyeight.com/polls/2016...    48922   
3      https://d25d2506sfb94s.cloudfront.net/cumulus_...    48687   
4      http://www.gravispolls.com/2016/11/final-natio...    48848   
8      http://projects.fivethirtyeight.com.s3.amazona...    48614   
...                                                  ...      ...   
10711  https://www.surveymonkey.com/elections/map?pol...    47892   
10726  https://www.surveymonkey.com/elections/map?pol...    47905   
10729  https://www.surveymonkey.com/elections/map?pol...    47916   
10800          https://luc.id/2016-presidential-tracker/    47163   
11071  https://www.scribd.com/document/328753246/NBC

Import assigned data

results = []

#for index, row in whole_data.iterrows():
    #row_index = 

#indices = whole_data.index[whole_data['poll_id'].isin()]

#need to find the index in poll_raw_years that corresponds to each poll_id, and then check if the the 'question_id' also corresponds, and the sample size
#but there will be multiple entries with each poll_id, question_id etc, so we need to check ALL with matching poll_id and
# keep only those that match all three of a given row in final_matched_set

# It might be easier to identify and append rows

# FINAL GOAL, append the column 'methodology' from 'poll_raw_years' to all matching entries in final_matched_set
# - so remove unmatching entries

In [13]:
mb_org_data = pd.read_csv('Dataset_assigned_data_taken_from\\president_general_polls_2016.csv')
# I have the FiveThirtyEight dataset one level deeper than the provided set within the folder laballed above

Import found data from FiveThirtyEight (testing if same dataset but raw)

In [14]:
as_data

state   startdate     enddate                  pollster grade  \
0          U.S.  2016-11-03  2016-11-06  ABC News/Washington Post    A+   
1          U.S.  2016-11-01  2016-11-07   Google Consumer Surveys     B   
2          U.S.  2016-11-02  2016-11-06                     Ipsos    A-   
3          U.S.  2016-11-04  2016-11-07                    YouGov     B   
4          U.S.  2016-11-03  2016-11-06          Gravis Marketing    B-   
...         ...         ...         ...                       ...   ...   
4203   Virginia  2016-09-16  2016-09-22                     Ipsos    A-   
4204  Wisconsin  2016-08-04  2016-08-07      Marquette University     A   
4205       Utah  2016-11-01  2016-11-07   Google Consumer Surveys     B   
4206     Oregon  2016-10-21  2016-11-02                     Ipsos    A-   
4207   Michigan  2016-01-23  2016-01-26                  EPIC-MRA    A-   

      samplesize population  rawpoll_clinton  rawpoll_trump  rawpoll_johnson  \
0         2220.0         lv            47.00          43.00             4.00   
1        26574.0         lv            38.03          35.69             5.46   
2         2195.0         lv            42.00          39.00             6.00   
3         3677.0         lv            45.00          41.00             5.00   
4        16639.0         rv            47.00          43.00             3.00   
...          ...        ...              ...            ...              ...   
4203       452.0         lv            46.54          40.04              NaN   
4204       683.0         lv            47.00          34.00             9.00   
4205       286.0         lv            21.33          35.05             9.99   
4206       446.0         lv            46.46          37.41              NaN   
4207       600.0         lv            43.00          41.00              NaN   

      rawpoll_mcmullin  adjpoll_clinton  adjpoll_trump  adjpoll_johnson  \
0                  NaN         45.20163       41.72430         4.626221   
1                  NaN         43.34557       41.21439         5.175792   
2                  NaN         42.02638       38.81620         6.844734   
3                  NaN         45.65676       40.92004         6.069454   
4                  NaN         46.84089       42.33184         3.726098   
...                ...              ...            ...              ...   
4203               NaN         46.47852       40.48017              NaN   
4204               NaN         48.74781       39.07778         4.705020   
4205               NaN         26.65200       40.57738         9.705791   
4206               NaN         45.12949       37.10720              NaN   
4207               NaN         42.14966       42.05508              NaN   

      adjpoll_mcmullin  
0                  NaN  
1                  NaN  
2                  NaN  
3                  NaN  
4                  NaN  
...                ...  
4203               NaN  
4204               NaN  
4205               NaN  
4206               NaN  
4207               NaN  

[4208 rows x 15 columns]

In [15]:
#mb_org_data

In [16]:
#Going to try graph between survey size and rating

fig = alt.Chart(as_data).mark_point().encode(x='grade',y='samplesize')

In [17]:
fplot = fig + fig.transform_regression('grade','samplesize').mark_line()

In [18]:
fplot
# clearly the extreme values are making the visualization worse. Let's see how many counts we have for each 5000 size range 

alt.LayerChart(...)

In [19]:
count = 0

for i in range(0,as_data.shape[0]):
    if as_data.loc[i,'samplesize'] > 10000:
        count += 1
    
print(count)

41


In [20]:
#Only 41 with over 10000, lets try with only sample sizes less than 10000

small_samples = as_data[as_data['samplesize']<10000]

In [21]:
# So seemingly no correlation between grade and sample size
fig2 = alt.Chart(small_samples).mark_point().encode(x='grade',y='samplesize')
fplot2 = fig2 + fig2.transform_regression('grade','samplesize').mark_line()
fplot2
# Notice how the 'A+' grade has seemingly smaller samplesizes, suggesting it's possible that better polls are signified
# not by more data, but instead by better practices in adjusting the data

alt.LayerChart(...)

In [22]:
datetime_object = dt.strptime(as_data.loc[1,'enddate'], '%Y-%m-%d')
datetime_object

datetime.datetime(2016, 11, 7, 0, 0)

In [23]:
as_data['startdate'] = as_data['startdate'].astype('datetime64')
as_data['enddate'] = as_data['enddate'].astype('datetime64')

In [24]:
as_data.loc[1,'enddate']-as_data.loc[1,'startdate']

Timedelta('6 days 00:00:00')

In [25]:
#Finding longest observation range
max_delt = as_data.loc[0,'enddate']-as_data.loc[0,'startdate']


for i in range(0,as_data.shape[0]):
    curr_delt = as_data.loc[i,'enddate']-as_data.loc[i,'startdate']
    if curr_delt > max_delt:
        max_delt=curr_delt
    
print(max_delt)

59 days 00:00:00



# Possible story to look into, more data DOES NOT EQUAL better results!

### Possible other story to look into - accuracy of polls for 'likely voters' vs 'rv' vs 'a' vs 'v'

- would want to look into how many of each there are, but more importantly, what the distribution of poll grades is within each

#This will make a 'timedelta64' type column with length of survey
#Adding column of length of survey
lengthofsurvey = [0]*as_data.shape[0]

for i in range(0,as_data.shape[0]):
    lengthofsurvey[i] = as_data.loc[i,'enddate']-as_data.loc[i,'startdate']
    
as_data['lengthofsurvey'] = lengthofsurvey
#as_data['lengthofsurvey']

In [26]:
#Adding column of length of survey (days_integer)
lengthofsurvey = [0]*as_data.shape[0]

for i in range(0,as_data.shape[0]):
    lengthofsurvey[i] = (as_data.loc[i,'enddate']-as_data.loc[i,'startdate']).total_seconds()/(60*60*24)
    
as_data['lengthofsurveydaysint'] = lengthofsurvey
#as_data = as_data.drop(columns = ['lengthofsurvey'])
#as_data = as_data.drop(columns = ['lengthofsurvey_days_int'])
#(as_data.loc[1, 'lengthofsurvey']).total_seconds()/(60*60*24)

In [27]:
alt.Chart(as_data).mark_bar().encode(
    alt.X("lengthofsurveydaysint:Q", bin=alt.Bin(extent=[0,60],step=4), title='Length of Survey (Days)'), 
                                     alt.Y('count()', title = 'Number of Surveys')
                                    )


alt.Chart(...)

In [28]:
as_data

state  startdate    enddate                  pollster grade  \
0          U.S. 2016-11-03 2016-11-06  ABC News/Washington Post    A+   
1          U.S. 2016-11-01 2016-11-07   Google Consumer Surveys     B   
2          U.S. 2016-11-02 2016-11-06                     Ipsos    A-   
3          U.S. 2016-11-04 2016-11-07                    YouGov     B   
4          U.S. 2016-11-03 2016-11-06          Gravis Marketing    B-   
...         ...        ...        ...                       ...   ...   
4203   Virginia 2016-09-16 2016-09-22                     Ipsos    A-   
4204  Wisconsin 2016-08-04 2016-08-07      Marquette University     A   
4205       Utah 2016-11-01 2016-11-07   Google Consumer Surveys     B   
4206     Oregon 2016-10-21 2016-11-02                     Ipsos    A-   
4207   Michigan 2016-01-23 2016-01-26                  EPIC-MRA    A-   

      samplesize population  rawpoll_clinton  rawpoll_trump  rawpoll_johnson  \
0         2220.0         lv            47.00          43.00             4.00   
1        26574.0         lv            38.03          35.69             5.46   
2         2195.0         lv            42.00          39.00             6.00   
3         3677.0         lv            45.00          41.00             5.00   
4        16639.0         rv            47.00          43.00             3.00   
...          ...        ...              ...            ...              ...   
4203       452.0         lv            46.54          40.04              NaN   
4204       683.0         lv            47.00          34.00             9.00   
4205       286.0         lv            21.33          35.05             9.99   
4206       446.0         lv            46.46          37.41              NaN   
4207       600.0         lv            43.00          41.00              NaN   

      rawpoll_mcmullin  adjpoll_clinton  adjpoll_trump  adjpoll_johnson  \
0                  NaN         45.20163       41.72430         4.626221   
1                  NaN         43.34557       41.21439         5.175792   
2                  NaN         42.02638       38.81620         6.844734   
3                  NaN         45.65676       40.92004         6.069454   
4                  NaN         46.84089       42.33184         3.726098   
...                ...              ...            ...              ...   
4203               NaN         46.47852       40.48017              NaN   
4204               NaN         48.74781       39.07778         4.705020   
4205               NaN         26.65200       40.57738         9.705791   
4206               NaN         45.12949       37.10720              NaN   
4207               NaN         42.14966       42.05508              NaN   

      adjpoll_mcmullin  lengthofsurveydaysint  
0                  NaN                    3.0  
1                  NaN                    6.0  
2                  NaN                    4.0  
3                  NaN                    3.0  
4                  NaN                    3.0  
...                ...                    ...  
4203               NaN                    6.0  
4204               NaN                    3.0  
4205               NaN                    6.0  
4206               NaN                   12.0  
4207               NaN                    3.0  

[4208 rows x 16 columns]